In [7]:
import pandas as pd
import numpy as np
from tqdm import tqdm
import plotly.express as px
from scipy.stats import ttest_ind
from sklearn.decomposition import PCA
import pickle

# set infinite display
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)

# allow tqdm to chart pandas progress
tqdm.pandas()

## This notebook contains the pipeline and all of its constituent tools.

### The dataframes need some further processing before the pipeline can run on them.

In [8]:
# import the TPM dataframe for the majority of the pipeline
TPM = pd.read_csv('../../results/TPM.tsv', sep='\t', index_col=0)

In [9]:
# import the TPM dataframe for the PCA analysis
TPM_pca = pd.read_csv('../../results/TPM.tsv', sep='\t', index_col=0)

### Processing the TPM dataframe for the statistical tools

In [10]:
# transpose the dataframe
TPM = TPM.T
#rename TPM index to read_group_id
TPM.index.names = ['read_group_id']
# turn the index into a column
TPM.reset_index(inplace=True)
#preview the dataframe only showing the first 10 columns
TPM.iloc[:, :10].head()

Name                         read_group_id  ENST00000456328.2  \
0     16e72993-470f-4ac2-91fe-562c61615a59           0.068287   
1     0a3c7dd6-cc30-416d-91f7-d91b22bbbff4           0.000000   
2     a3a21562-3933-4e92-8ea4-70be74dc19fe           0.000000   
3     baefbbf5-b891-4dd7-8be3-f6f28f0b24f7           0.000000   
4     c1d7f3a1-350b-4e57-a02d-4313e4beabe4           0.000000   

Name  ENST00000450305.2  ENST00000488147.1  ENST00000619216.1  \
0                   0.0           1.660365                0.0   
1                   0.0           2.053805                0.0   
2                   0.0           3.124912                0.0   
3                   0.0           1.658161                0.0   
4                   0.0           0.948201                0.0   

Name  ENST00000473358.1  ENST00000469289.1  ENST00000607096.1  \
0              0.000000                0.0                0.0   
1              0.000000                0.0                0.0   
2              0.040398                0.0                0.0   
3              0.000000                0.0                0.0   
4              0.000000                0.0                0.0   

Name  ENST00000417324.1  ENST00000461467.1  
0                   0.0                0.0  
1                   0.0                0.0  
2                   0.0                0.0  
3                   0.0                0.0  
4                   0.0                0.0

In [11]:
#load metadata dataframe
metadata = pd.read_csv('../../results/metadata.tsv', sep='\t')
#preview the dataframe only showing the first 10 columns
metadata.iloc[:, :10].head()

case_id                            aliquot_id  \
0  5705efcc-b48f-435c-8a28-9e0d407ecadd  75ac0619-947a-427b-a53f-71e121a7ec8f   
1  5705efcc-b48f-435c-8a28-9e0d407ecadd  948c4d53-3d91-48a6-bec4-0cc96020e572   
2  763e0702-8379-4b5e-95d1-a84f412c51e7  ce810e2e-4929-4bbc-95ff-6da493477391   
3  763e0702-8379-4b5e-95d1-a84f412c51e7  33c921ea-b743-4d32-9c56-875de6028c71   
4  763e0702-8379-4b5e-95d1-a84f412c51e7  173c0d6a-bc67-4a72-b6d3-b2a411e24785   

                          read_group_id has_blood_cancer tissue_type  \
0  71894d8b-5210-44dc-aadc-a199d3843dd2            False       Tumor   
1  86774648-bb57-42c3-b835-9fb11b590d8b            False       Tumor   
2  c2980255-7c57-4b79-82a7-f77098ff164e            False       Tumor   
3  8062c6e4-d501-4c91-ab02-f36f4e7fd387            False       Tumor   
4  39c8b5e7-ac68-4009-ab82-e1ee495bdbd9            False      Normal   

      instrument_model  RIN includes_spike_ins  \
0  Illumina HiSeq 4000  NaN               True   
1                  NaN  NaN                NaN   
2  Illumina HiSeq 4000  NaN               True   
3  Illumina HiSeq 4000  NaN               True   
4  Illumina HiSeq 4000  NaN               True   

                        library_preparation_kit_name  \
0  TruSeq Stranded Total RNA Library Prep Kit wit...   
1                                                NaN   
2  TruSeq Stranded Total RNA Library Prep Kit wit...   
3  TruSeq Stranded Total RNA Library Prep Kit wit...   
4  TruSeq Stranded Total RNA Library Prep Kit wit...   

  library_preparation_kit_vendor  
0                       Illumina  
1                            NaN  
2                       Illumina  
3                       Illumina  
4                       Illumina

In [12]:
# Convert 'read_group_id' to the same data type in both DataFrames
metadata['read_group_id'] = metadata['read_group_id'].astype(str)

# Check if 'read_group_id' is present in TPM dataframe
if 'read_group_id' in TPM.columns:
    TPM['read_group_id'] = TPM['read_group_id'].astype(str)
    # Merge TPM and metadata DataFrames on read_group_id
    TPM = pd.merge(TPM, metadata[['case_id', 'read_group_id']], on='read_group_id', how='left')
else:
    print("read_group_id column not found in TPM dataframe")

In [13]:
#move case_ID to 1st column 
TPM = TPM[['case_id'] + [col for col in TPM.columns if col != 'case_id']]
#remove duplicate case_id's from TPM dataframe
TPM.drop_duplicates(subset='case_id', keep='first', inplace=True)
#sort by case_id
TPM.sort_values(by=['case_id'], inplace=True)
#remove read_group_id column
TPM.drop(columns=['read_group_id'], inplace=True)
# remove the . and everything after it from the transcript_id columns in the TPM dataframe
TPM.columns = [col.split('.')[0] for col in TPM.columns]
#preview first 10 columns of TPM dataframe
TPM.iloc[:, :10].head()

case_id  ENST00000456328  ENST00000450305  \
157  020db2d3-bb73-46c7-89ea-4648e0d3f2cb              0.0              0.0   
311  0215c1e2-70aa-495b-a1f1-25bd989a9f12              0.0              0.0   
579  02208cc6-6221-4e84-bf66-2d32fb49a358              0.0              0.0   
576  022c3490-811c-4f82-ad9b-8004a3df7e5c              0.0              0.0   
584  026644c2-a548-4f0d-95bf-716c567f055c              0.0              0.0   

     ENST00000488147  ENST00000619216  ENST00000473358  ENST00000469289  \
157         3.514290              0.0         0.000000         0.000000   
311         2.866582              0.0         0.000000         0.000000   
579         1.398049              0.0         0.000000         0.000000   
576         1.903676              0.0         0.000000         0.000000   
584         3.724858              0.0         0.123148         0.053909   

     ENST00000607096  ENST00000417324  ENST00000461467  
157              0.0              0.0              0.0  
311              0.0              0.0              0.0  
579              0.0              0.0              0.0  
576              0.0              0.0              0.0  
584              0.0              0.0              0.0

### Processing the TPM dataframe for PCA analysis

In [14]:
# print shape of dataframe
print('Before removing non-performing transcripts: ', TPM_pca.shape)
# find genes with 0 TPM in all samples
TPM_pca = TPM_pca.loc[(TPM_pca != 0).any(axis=1)]
# print shape of dataframe
print('After removing non-performing transcripts: ', TPM_pca.shape)

# transpose the dataframe
TPM_pca = TPM_pca.T

# Flatten the DataFrame to a 1D array
flat_values = TPM_pca.values.flatten()

# Calculate mean and standard deviation
mean_value = np.mean(flat_values)
std_value = np.std(flat_values)

# calculate max, min and range
max_value = np.max(flat_values)
min_value = np.min(flat_values)
range_value = max_value - min_value

# print all statistical values
print('Mean TPM: ', mean_value)
print('Standard deviation TPM: ', std_value)
print('Max TPM: ', max_value)
print('Min TPM: ', min_value)
print('Range TPM: ', range_value)

# find the smallest non-zero value in the flattened TPM array
smallest_nonzero = np.min(TPM_pca.values[TPM_pca.values > 0])
# print the smallest non-zero value
print('Smallest non-zero TPM value: ', smallest_nonzero)

Before removing non-performing transcripts:  (252045, 888)
After removing non-performing transcripts:  (244124, 888)
Mean TPM:  4.096278940190421
Standard deviation TPM:  648.180788803733
Max TPM:  406495.657207
Min TPM:  0.0
Range TPM:  406495.657207
Smallest non-zero TPM value:  1e-06


In [15]:
# introduce pseudocount
TPM_pca = TPM_pca + 0.000000001
# perform log-transformation
TPM_pca = TPM_pca.progress_apply(np.log2)

100%|██████████| 244124/244124 [00:25<00:00, 9471.96it/s] 


In [16]:
# perform PCA
pca = PCA(n_components=3, whiten=True)
pca.fit(TPM_pca)

# transform the data
TPM_pca_fit = pca.transform(TPM_pca)

# create a dataframe with the PCA results
TPM_pca_df = pd.DataFrame(data = TPM_pca_fit, columns = ['PC1', 'PC2', 'PC3'], index=TPM_pca.index)

# give the index column the name 'read_group_id'
TPM_pca_df.index.name = 'read_group_id'
# transform the index header of TPM_pca_df into a column
TPM_pca_df.reset_index(inplace=True)

### Selecting a subset of relevant metadata columns to make the query process easier.

In [17]:
# take tissue_type, gender, race, age_at_diagnosis, ajcc_pathologic_stage, primary_diagnosis, morphology, tissue_or_organ_of_origin, tumor_focality, disease_type, primary_site from the metadata and merge it with the TPM_pca_df into a new dataframe called TPM_pre_cluster
columns = ['case_id', 'tissue_type', 'gender', 'race', 'age_at_diagnosis', 'ajcc_pathologic_stage', 'primary_diagnosis', 'tissue_or_organ_of_origin', 'tumor_focality', 'disease_type', 'primary_site']
# Create a new dataframe with selected columns from metadata
selected_metadata = metadata[columns]
#remove duplicate case_id's from selected metadata dataframe
selected_metadata.drop_duplicates(subset='case_id', keep='first', inplace=True)
# preview the dataframe
selected_metadata.head()

/var/folders/n5/_h8qqt011vq0417yxq9kch240000gq/T/ipykernel_73096/3655264761.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  selected_metadata.drop_duplicates(subset='case_id', keep='first', inplace=True)


case_id tissue_type  gender   race  \
0  5705efcc-b48f-435c-8a28-9e0d407ecadd       Tumor  female  white   
2  763e0702-8379-4b5e-95d1-a84f412c51e7       Tumor  female  white   
5  8710ce04-6b7f-4e37-adc0-0df1f2798b30       Tumor    male  asian   
7  c1898677-7a92-48cf-a09f-71d91c1cf8dc       Tumor  female  white   
8  e1d68cfb-04e7-43cb-b8c5-b523cf917636       Tumor    male  white   

   age_at_diagnosis ajcc_pathologic_stage                 primary_diagnosis  \
0           22142.0               Stage I  Endometrioid adenocarcinoma, NOS   
2           22179.0              Stage II         Renal cell carcinoma, NOS   
5           20772.0              Stage IB               Adenocarcinoma, NOS   
7           21979.0             Stage IIB  Infiltrating duct carcinoma, NOS   
8           23545.0             Stage IVA      Squamous cell carcinoma, NOS   

  tissue_or_organ_of_origin tumor_focality                  disease_type  \
0              Corpus uteri       Unifocal  Adenomas and Adenocarcinomas   
2               Kidney, NOS       Unifocal  Adenomas and Adenocarcinomas   
5                 Lung, NOS       Unifocal  Adenomas and Adenocarcinomas   
7          Head of pancreas       Unifocal  Ductal and Lobular Neoplasms   
8               Larynx, NOS       Unifocal       Squamous Cell Neoplasms   

                  primary_site  
0                  Uterus, NOS  
2                       Kidney  
5            Bronchus and lung  
7                     Pancreas  
8  Other and ill-defined sites

In [18]:
# introduce case_id to TPM_pca_df
TPM_pca_df = pd.merge(TPM_pca_df, metadata[['case_id', 'read_group_id']], on='read_group_id', how='left')
# Merge selected_metadata with TPM_pca_df using the 'read_group_id' column
TPM_pca_pipeline = pd.merge(TPM_pca_df, selected_metadata, on='case_id')
# drop the read_group_id column
TPM_pca_pipeline.drop(columns=['read_group_id'], inplace=True)
# remove duplicate case_id's from TPM_pca_pipeline dataframe
TPM_pca_pipeline.drop_duplicates(subset='case_id', keep='first', inplace=True)

### Loading the gene_name dictionaries.

In [19]:
with open('../../results/gene_to_transcript_mapping.pkl', 'rb') as file:
    gene_to_transcript_mapping = pickle.load(file)
with open('../../results/transcript_to_gene_mapping.pkl', 'rb') as file:
    transcript_to_gene_mapping = pickle.load(file)

## This is where we define the pipeline functions. Later on, these will be moved to python scripts and an argument parser will be built to control their execution from a CLI.

In [54]:
def query_maker(dataframe, TPM_dataframe, PCA_dataframe):
    # print the column names, except for the first column
    print(dataframe.columns[1:])
    # prompt for a column name
    column = input('Enter a column name: ')
    # check if value is numerical or categorical
    # if numerical, display range of values and prompt for a threshold
    if dataframe[column].dtype == np.float64 or dataframe[column].dtype == np.int64:
        # print the range of values
        print('Range of values: ', dataframe[column].min(), ' - ', dataframe[column].max())
        # prompt for a threshold
        threshold = float(input('Enter a threshold: '))
        # subset the dataframe into two dataframes based on the threshold
        dataframe1 = dataframe.loc[dataframe[column] < threshold]
        dataframe2 = dataframe.loc[dataframe[column] >= threshold]
        # print the shape of the two dataframes
        print('Dataframe 1 shape: ', dataframe1.shape)
        print('Dataframe 2 shape: ', dataframe2.shape)
        # use the case_id column to subset the TPM dataframe
        TPM_dataframe1 = TPM_dataframe[TPM_dataframe['case_id'].isin(dataframe1['case_id'])]
        TPM_dataframe2 = TPM_dataframe[TPM_dataframe['case_id'].isin(dataframe2['case_id'])]
        # use the case_ids in dataframe1 to add a column to the PCA dataframe
        PCA_dataframe['group'] = PCA_dataframe['case_id'].isin(dataframe1['case_id'])
        # use the groups to generate a PCA plot
        fig = px.scatter_3d(PCA_dataframe, x='PC1', y='PC2', z='PC3', color='group', hover_name='case_id', title=f'PCA plot of {column} with threshold {threshold}')
        fig.show()
        # return the two dataframes
        return TPM_dataframe1, TPM_dataframe2
    # if categorical, display unique values and prompt for a value
    elif dataframe[column].dtype == np.object:
        print(dataframe[column].value_counts())
        #make an empty list to store selected values until user says stop
        selected_values = []
        #make a variable to store user input
        user_input = ''
        #make a while loop that will continue until user says stop
        while user_input != 'stop':
            #prompt user for input
            user_input = input('Enter a value or type stop: ')
            #add user input to selected values list
            selected_values.append(user_input)
        #remove stop from selected values list
        selected_values.remove('stop')
        #subset the dataframe into two dataframes based on the selected values
        dataframe1 = dataframe.loc[dataframe[column].isin(selected_values)]
        dataframe2 = dataframe.loc[~dataframe[column].isin(selected_values)]
        # print the shape of the two dataframes
        print('Dataframe 1 shape: ', dataframe1.shape)
        print('Dataframe 2 shape: ', dataframe2.shape)
        # use the case_id column to subset the TPM dataframe
        TPM_dataframe1 = TPM_dataframe[TPM_dataframe['case_id'].isin(dataframe1['case_id'])]
        TPM_dataframe2 = TPM_dataframe[TPM_dataframe['case_id'].isin(dataframe2['case_id'])]
        # use the case_ids in dataframe1 to add a column to the PCA dataframe
        PCA_dataframe['group'] = PCA_dataframe['case_id'].isin(dataframe1['case_id'])
        # use the groups to generate a PCA plot
        fig = px.scatter_3d(PCA_dataframe, x='PC1', y='PC2', z='PC3', color='group', hover_name='case_id', title=f'PCA plot of {column} with values {selected_values}')
        fig.show()
        # return the two dataframes
        return TPM_dataframe1, TPM_dataframe2

def ttester(df1, df2, alpha=0.05):
    # Remove the first columns from the dataframes
    df1 = df1.iloc[:, 1:]
    df2 = df2.iloc[:, 1:]
    
    # Run a t-test on each column
    ttest_results = df1.progress_apply(lambda x: ttest_ind(x, df2.loc[:, x.name]))
    
    # Create a DataFrame for the results
    ttest_df = pd.DataFrame({
        # 'transcript_id' will be the column names of ttest_results
        'transcript_id': ttest_results.columns,
        # 't_statistic' will be the first row of ttest_results
        't_statistic': ttest_results.iloc[0],
        # 'p_value' will be the second row of ttest_results
        'p_value': ttest_results.iloc[1]
    })

    # reset the index of ttest_df
    ttest_df.reset_index(drop=True, inplace=True)
    
    # Adjust the significance level (alpha) based on the number of tests
    significance_level = alpha / len(ttest_df)

    # Identify the statistically significant tests after Bonferroni correction
    ttest_df['significant'] = ttest_df['p_value'] < significance_level

    # Sort the dataframe by p-value
    ttest_df.sort_values(by='p_value', inplace=True)

    # Count the number of significant transcripts
    significant_transcripts = ttest_df['significant'].sum()
    # Print the number of significant transcripts
    print('Significant transcripts (using ttests): ', significant_transcripts)
    # print head
    print(ttest_df.head())
    return ttest_df

def gene_aggregator(ttest_df, gene_map):
    # Convert gene_map to a Series for faster mapping
    gene_map_series = pd.Series(gene_map)
    # gene_map_series.replace('', 'Unknown', inplace=True)
    # Map transcript_id to gene_name
    ttest_df['gene_name'] = ttest_df['transcript_id'].map(gene_map_series)
    # Group by gene_name and find the index of the maximum p_value in each group
    idx = ttest_df.groupby('gene_name')['p_value'].idxmax()
    idx = idx[~np.isnan(idx)]
    # Use the index to extract the corresponding rows from the original DataFrame
    gene_level_results = ttest_df.loc[idx, ['gene_name', 'p_value', 't_statistic', 'significant']]
    # Resetting the index if needed
    gene_level_results.reset_index(drop=True, inplace=True)
    # Fill missing gene names with 'Unknown'
    #gene_level_results['gene_name'].fillna('Unknown', inplace=True)
    # Sort the DataFrame by p-value
    gene_level_results.sort_values(by='p_value', inplace=True)
    # Count the number of significant genes
    significant_genes = gene_level_results['significant'].sum()
    # Print the number of significant genes
    print('Significant genes (using idxmax): ', significant_genes)
    # Print the head of the DataFrame
    print(gene_level_results.head())
    # Return the gene_level_results DataFrame
    return gene_level_results

def visualizer(df1, df2, genemap, gene_level_results_df):
    # remove the first columns from the dataframes
    df1 = df1.iloc[:, 1:]
    df2 = df2.iloc[:, 1:]

    results = []

    for gene, transcripts in tqdm(genemap.items()):
        # Extract the relevant columns from the TPM dataframe
        gene_data1 = df1[transcripts]
        gene_data2 = df2[transcripts]
        # get sums
        sum1 = gene_data1.sum(axis=1)
        sum2 = gene_data2.sum(axis=1)
        # get means
        mean1 = sum1.mean()
        mean2 = sum2.mean()
        # get log 2 fold change
        if mean1 == 0 or mean2 == 0:
            log2_fold_change = np.nan
        else:
            log2_fold_change = np.log2(mean2/mean1)
        # get vectors
        v_mean1 = gene_data1.mean(axis=0)
        v_mean2 = gene_data2.mean(axis=0)
        # get euclidean distance of mean vectors
        euclidean_distance = np.linalg.norm(v_mean1 - v_mean2)
        # add log2_fold_change and euclidean_distance to results
        results.append({'gene_name': gene, 'log2_fold_change': log2_fold_change, 'euclidean_distance': euclidean_distance})

    # Convert results to a DataFrame
    mean_df = pd.DataFrame(results)
    # Merge mean_df with gene_level_results_df
    mean_df = pd.merge(mean_df, gene_level_results_df[['gene_name', 'significant']], on='gene_name', how='left')
    
    # use mean_df to create a scatter plot, x = log2_fold_change, y = euclidean_distance, and make another one where the y-axis should be log scaled, display both plots
    fig = px.scatter(mean_df, x='log2_fold_change', y='euclidean_distance', hover_name='gene_name', color='significant', title='log2_fold_change vs euclidean_distance')
    fig.show()
    fig = px.scatter(mean_df, x='log2_fold_change', y='euclidean_distance', hover_name='gene_name', color='significant', title='log2_fold_change vs euclidean_distance', log_y=True)
    fig.show()

### A complete execution example, using disease_type = Adenomas and Adenocarcinomas vs all other disease_types.

In [55]:
# define a master function that runs all the functions
def master(metadata, TPM, PCA_dataframe, gene_map, transcript_map):
    # run query_maker to get two dataframes
    TPM_dataframe1, TPM_dataframe2 = query_maker(metadata, TPM, PCA_dataframe)
    # run ttester to get a ttest_df
    ttest_df = ttester(TPM_dataframe1, TPM_dataframe2, alpha=0.05)
    # run gene_aggregator to get a gene_level_results_df
    gene_level_results_df = gene_aggregator(ttest_df, transcript_map)
    # run visualizer to get a plot
    visualizer(TPM_dataframe1, TPM_dataframe2, gene_map, gene_level_results_df)
    # return ttest_df and gene_level_results_df
    return ttest_df, gene_level_results_df

In [57]:
# run master function on the dataframe
ttest_df, genelevel_df = master(selected_metadata, TPM, TPM_pca_pipeline, gene_to_transcript_mapping, transcript_to_gene_mapping)

Index(['tissue_type', 'gender', 'race', 'age_at_diagnosis',
       'ajcc_pathologic_stage', 'primary_diagnosis',
       'tissue_or_organ_of_origin', 'tumor_focality', 'disease_type',
       'primary_site'],
      dtype='object')


/var/folders/n5/_h8qqt011vq0417yxq9kch240000gq/T/ipykernel_73096/2861982683.py:30: DeprecationWarning:

`np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations



Adenomas and Adenocarcinomas            810
Squamous Cell Neoplasms                 352
Gliomas                                 234
Ductal and Lobular Neoplasms            181
Myeloid Leukemias                       179
Nevi and Melanomas                      168
Soft Tissue Tumors and Sarcomas, NOS    121
Not Applicable                           27
Name: disease_type, dtype: int64
Dataframe 1 shape:  (810, 11)
Dataframe 2 shape:  (1263, 11)


100%|██████████| 252045/252045 [01:00<00:00, 4179.94it/s]


Significant transcripts (using ttests):  25472
          transcript_id  t_statistic       p_value  significant
74170   ENST00000506445    19.833544  2.350783e-71         True
233223  ENST00000371610    19.520365  1.485414e-69         True
101921  ENST00000537763    19.017980  1.094969e-66         True
246811  ENST00000542398    18.573721  3.566358e-64         True
10049   ENST00000260506    18.544867  5.183790e-64         True
Significant genes (using idxmax):  1324
        gene_name       p_value  t_statistic  significant
23550      PRKAA2  3.550405e-48    15.628493         True
27144  RPH3AL-AS2  9.498380e-46    15.158439         True
13706   LAMTOR5P1  1.346460e-45    15.128836         True
4703        CLDN3  2.289406e-44    14.887274         True
7610        ENPP4  6.048387e-44    14.803951         True


100%|██████████| 40604/40604 [00:43<00:00, 923.96it/s]
